# SourceList and AssociateList Exercises

For the OmegaCAM data used in earlier exercises, make a SourceList each for 2 ReducedScienceFrames (they overlap). Set the SExtractor detection threshold to 6.0
Lets find the ReducedScienceFrames we made earlier and pick two:

In [ ]:
context.set_project('TUTORIAL')
context.set_privileges(1)
print(context.get_current_project())

In [ ]:
reds = (ReducedScienceFrame.chip.name == 'ESO_CCD_#65').user_only().project_only()
filename1 = reds[0].filename
filename2 = reds[1].filename
p = Pars(SourceList, instrument='OMEGACAM')
p.SourceList.sexconf.DETECT_THRESH = 6.0
pars = p.get()
task = SourceListTask(filenames=[filename1], pars=pars, commit=1)
task.execute()
task = SourceListTask(filenames=[filename2], pars=pars, commit=1)
task.execute()

For one of the SourceLists you just made, obtain the number of sources in the sourcelist, find the brightest source, and obtain its half-light radius.
The final line printed by the task should have displayed the SourceList identifier (SLID), which can be used to query directly (use your own SLID instead of the one below):

In [ ]:
sl = (SourceList.SLID == SLID)[0]

Alternatively, select the most recent SourceList created by yourself:

In [ ]:
sl = (SourceList.SLID > 61771701).user_only().max('SLID')

Get the information from the SourceList:

In [ ]:
print(sl.number_of_sources)
magsid = [(src['MAG_ISO'], src['SID']) for src in sl.sources]
magsid.sort()
print(magsid[0])
sl.sources[230]['SID'], sl.sources[230]['FLUX_RADIUS']

Find out the piece of sky covered by the USNO catalogue in the database.

In [ ]:
usno = (SourceList.name == 'USNO-A2.0')[0]
RA, DEC = usno.sources.RA, usno.sources.DEC
print(max(RA), min(DEC), min(RA), max(DEC))

This is the current coverage as of 7/7/2014 of the USNO-A2.0 catalogue in the Astro-WISE database.
Find the B and R mags of the sources in the USNO catalog which are inside a distance of 0.1 degrees of position (12.0&deg;, -29.0&deg;)

In [ ]:
print(usno.info())
attrs = { 'RA': [], 'DEC': [], 'USNO_RMAG': [], 'USNO_BMAG': [] }
area = (12.0, -29.0, 0.1)
r = usno.sources.area_search(Area=area, attr_dict=attrs)
nos = len(r[usno.SLID])
for k in range(nos): print(attrs['RA'][k], attrs['DEC'][k], attrs['USNO_BMAG'][k], attrs['USNO_RMAG'][k])

AssociateLists are (among others) used for the Global Astrometric Solution. Lets find which sources are the same in the two SourceLists we have made:

In [ ]:
task = AssociateListTask(ids=[(SLID1, 's'), (SLID2, 's')], commit=True)
task.execute()

As before, the final line printed by the task shows the AssociateList identifier (ALID). Get it:

In [ ]:
al = (AssociateList.ALID == ALID)[0]

Check the sourcelists it has been made from are the ones created above and find out the pointing of the telescope and CCD names of the exposures used.

In [ ]:
for sl in al.sourcelists: print(sl.SLID, sl.frame.chip.name, sl.frame.astrom.CRVAL1, sl.frame.astrom.CRVAL2)